In [192]:
### Only run if needed (probably not needed)
!pip install plotly
!pip install "jupyterlab>=3" "ipywidgets>=7.6"
!pip install jupyter-dash
!pip install pandas
### You may need to restart jupyter lab for the changes to take effect

zsh:1: command not found: pip


zsh:1: command not found: pip
zsh:1: command not found: pip
zsh:1: command not found: pip


In [193]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go

The next two cells draw a graph of how many students of different types received their hall preferences

In [194]:
#import data from csv and store on pandas dataframe
allocate = pd.read_csv('results/datasetC_result_3.csv')
dataset = pd.read_csv('datasetC_with_roommate_pref.csv')
room_data = pd.read_csv('final_room_data.csv')

total_room = room_data['room_id'].count()
match_pref = 0
numOfgot = 0
total = allocate['Assigned Rooms'].count()
total_student = dataset['name'].count()

total_fre = dataset['student_year'].value_counts()['Freshman']
total_acc = dataset['accessibility_need'].value_counts()[1]
total_inc = dataset['low_income_status'].value_counts()[1]

got_acc = 0
got_inc = 0

got_fre = 0

pre_acc = 0
pre_inc = 0

pre_fre = 0

unit = len(allocate['Assigned Rooms'].value_counts())

visited = []

assigned_room = 0
visited_room = []


allo = -1
total_points = 0
for a in allocate['RUID']:
    allo += 1
    room_info = allocate.loc[allo,'Assigned Rooms']
    if pd.isna(room_info):
        allo -= 1
        continue
    building = room_info.split(",")[0]
    roomid = room_info.split(",")[2]
    row = dataset[dataset['RUID'] == a].index[0]
    if dataset.loc[row,'student_year'] == 'Freshman':
        got_fre += 1
        if building in dataset.loc[row, 'preferred_hall_ids']:
            pre_fre += 1
    if dataset.loc[row, 'accessibility_need'] == 1:
        got_acc += 1
        if building in dataset.loc[row, 'preferred_hall_ids']:
            pre_acc += 1
    if dataset.loc[row, 'low_income_status'] == 1:
        got_inc += 1
        if building in dataset.loc[row, 'preferred_hall_ids']:
            pre_inc += 1
    if building in dataset.loc[row, 'preferred_hall_ids']:
        match_pref += 1
print(total_student)
print(total_points)


5330
0


In [195]:

got_room = total / total_student
got_pre = match_pref / total_student


need_got = got_acc / total_acc
income_got = got_inc / total_inc
fir_got = got_fre / total_fre
need_pre = pre_acc / total_acc
income_pre = pre_inc / total_inc
fir_pre = pre_fre / total_fre

per_unit = unit / total_room

fig = go.Figure(data=go.Scatterpolar(
  r=[got_room, got_pre, need_got, income_got, fir_got, need_pre, income_pre, fir_pre, per_unit],
  theta=['percentage of assigned a room for all students','percentage of assigned a room that match all their preference for all students',
         'percentage of accessibility need students assigned a room', 'percentage of low income status students assigned a room',
           'percentage of 1st year students assigned a room','percentage of assigned a room that match all their preference for accessibility need students',
         'percentage of low income status students assigned a room that match all their preference for all students',
           'percentage of 1st year students assigned a room that match all their preference for all students', 'percentage of assigned rooms'],
  fill='toself'
))

fig.update_layout(
  polar=dict(
    radialaxis=dict(
      visible=True
    ),
  ),
  showlegend=False
)

fig.show()



This code gives some example evaluation metrics and how to test them, you shouold add more of your own (for example the other amenities and hall preferences).

In [196]:
def eval_fit(student, room):
  # print(student, room)
  
  if int(student.accessibility_need) and not int(room.has_accessibility_ramps):
    return 0
  if int(student.max_price) > int(room.price):
    return 0
  num_amenties = 2
  has_amenities = 1
  penalty = 0.5 / num_amenties
  if int(student.is_private_bathroom_preferred) and not int(room.has_private_bathroom):
    has_amenities -= penalty
  if int(student.laundry_availibility) and not int(room.has_laundry):
    has_amenities -= penalty

  return has_amenities
def roomate_points(student_data, allocated, room_data):
  points = 0
  possible_points = 0
  for student in student_data['RUID']:
    student = student_data[student_data['RUID'] == student].head(1)
    # print(student['roommate_preferences'] == '[]')
    # print((student['roommate_preferences'] == '[]').iloc[0])
    if (student['roommate_preferences'] == '[]').iloc[0]:
      continue
    else:
      pref = str(student['roommate_preferences'].iloc[0])[1:-1].split(',')
      satisfied = 0
      total = len(pref)
      for roomate in pref:
        roomate_room= allocated[allocated['RUID'] == int(roomate)]['Assigned Rooms'].item()
        my_room = allocated[allocated['RUID'] == int(student['RUID'])]['Assigned Rooms'].item()
        if pd.isna(roomate_room) or pd.isna(my_room):
          continue
        if my_room[:my_room.rindex('-')] == roomate_room[:roomate_room.rindex('-')]:
          print(roomate_room, my_room)
          satisfied += 1
      # print(pref)
      possible_points += 1
      points += satisfied / total
    # print(student)
  return (points / possible_points) * 1000


#import data from csv and store on pandas dataframe
allocate = pd.read_csv('results/datasetC_result_3.csv')
dataset = pd.read_csv('datasetC_with_roommate_pref.csv')
room_data = pd.read_csv('final_room_data.csv')

total_room = room_data['room_id'].count()
match_pref = 0
numOfgot = 0
total = allocate['Assigned Rooms'].count()
total_student = dataset['name'].count()

total_fre = dataset['student_year'].value_counts()['Freshman']
total_acc = dataset['accessibility_need'].value_counts()[1]
total_inc = dataset['low_income_status'].value_counts()[1]

got_acc = 0
got_inc = 0

got_fre = 0

pre_acc = 0
pre_inc = 0

pre_fre = 0

unit = len(allocate['Assigned Rooms'].value_counts())

visited = []

assigned_room = 0
visited_room = []


allo = -1
total_points = 0

#this shows how often we satify roomate preferences
for a in allocate['RUID']:
    allo += 1
    room_info = allocate.loc[allo,'Assigned Rooms']
    if pd.isna(room_info):
        allo -= 1
        continue
    building = room_info.split(",")[0].replace('[', '').replace(',', '').replace("'", "").strip()
    roomid = room_info.split(",")[2].replace(']', '').replace(',', '').replace("'", "").strip()
    subbuilding = room_info.split(",")[1].replace("'", "").strip()
    # print(building, roomid)
    if subbuilding == 'nan':
      room_info = room_data[(room_data.hall_id == building) & (room_data.room_id == roomid)].reset_index()
    else:
      room_info = room_data[(room_data.hall_id == building) & (room_data.room_id == roomid) & (room_data.building_id == subbuilding)].reset_index()
    if len(room_info) != 1:
      print(allocate.loc[allo,'Assigned Rooms'], room_info, student_info)
      break
    student_info = dataset[dataset['RUID'] == a].head(1)
    total_points += eval_fit(student_info, room_info)
print(f'this match got {total_points} out of {allo + 1} for amenities and accomadations')
print(f'this match got {roomate_points(dataset, allocate, room_data)} out of 1000 for roomate matching')


/var/folders/h2/g860m6f542l3g35r_zzkv9qw0000gn/T/ipykernel_2500/522835913.py:5: FutureWarning:

Calling int on a single element Series is deprecated and will raise a TypeError in the future. Use int(ser.iloc[0]) instead

/var/folders/h2/g860m6f542l3g35r_zzkv9qw0000gn/T/ipykernel_2500/522835913.py:7: FutureWarning:

Calling int on a single element Series is deprecated and will raise a TypeError in the future. Use int(ser.iloc[0]) instead

/var/folders/h2/g860m6f542l3g35r_zzkv9qw0000gn/T/ipykernel_2500/522835913.py:12: FutureWarning:

Calling int on a single element Series is deprecated and will raise a TypeError in the future. Use int(ser.iloc[0]) instead

/var/folders/h2/g860m6f542l3g35r_zzkv9qw0000gn/T/ipykernel_2500/522835913.py:14: FutureWarning:

Calling int on a single element Series is deprecated and will raise a TypeError in the future. Use int(ser.iloc[0]) instead

/var/folders/h2/g860m6f542l3g35r_zzkv9qw0000gn/T/ipykernel_2500/522835913.py:5: FutureWarning:

Calling int on a s

this match got 2523.0 out of 5330 for amenities and accomadations
['TS', nan, '4305-C'] ['TS', nan, '4305-E']
['TS', nan, '4305-E'] ['TS', nan, '4305-C']
['NCA', 'Apt 3820', '43-B'] ['NCA', 'Apt 3820', '43-C']
['BS', 'West', '312B-B'] ['BS', 'West', '312B-D']
['BS', 'West', '312B-D'] ['BS', 'West', '312B-B']
this match got 0.6256256256256256 out of 1000 for roomate matching


In [197]:
def compute_percentage_priced_out(student_data, allocated, room_data):
    priced_out_count = len(student_data)
    total_students = len(student_data)
    allo = -1
    for student_ruid in allocated['RUID']:
        allo += 1
        room_info = allocate.loc[allo,'Assigned Rooms']
        if pd.isna(room_info):
            allo -= 1
            priced_out_count -= 1
            continue
        room_info = allocated[allocated['RUID'] == student_ruid]['Assigned Rooms']
        room_info_str = allocated[allocated['RUID'] == student_ruid]['Assigned Rooms'].item()
        building, subbuilding, roomid = [x.strip().replace('[', '').replace(']', '').replace("'", "") for x in room_info_str.split(",")]

        if subbuilding == 'nan':
            room_info = room_data[(room_data.hall_id == building) & (room_data.room_id == roomid)].reset_index().iloc[0]
        else:
            room_info = room_data[(room_data.hall_id == building) & (room_data.room_id == roomid) & (room_data.building_id == subbuilding)].reset_index().iloc[0]
        
        student_info = student_data[student_data['RUID'] == student_ruid].head(1).iloc[0]

        if int(student_info.max_price) < int(room_info.price):
            priced_out_count -= 1

    return (priced_out_count)

percentage_priced_out = compute_percentage_priced_out(dataset, allocate, room_data)
print(f"This match got {percentage_priced_out} out of {allo + 1} for students kept within price")


This match got 2756 out of 5330 for students kept within price


In [198]:
def compute_sophomores_allocated_housing(student_data, allocated):
    sophomores_allocated_count = 0
    allo = -1
    for student_ruid in allocated['RUID']:
        allo += 1
        room_info = allocate.loc[allo,'Assigned Rooms']
        if pd.isna(room_info):
            allo -= 1
            continue
        room_info = allocated[allocated['RUID'] == student_ruid]['Assigned Rooms']
        student_info = student_data[student_data['RUID'] == student_ruid].head(1).iloc[0]

        if student_info['student_year'] == 'Sophomore':
            sophomores_allocated_count += 1

    return sophomores_allocated_count

number_of_sophomores_allocated = compute_sophomores_allocated_housing(dataset, allocate)
total_sophomores = len(dataset[dataset['student_year'] == 'Sophomore'])

print(f"This match got {number_of_sophomores_allocated} out of {total_sophomores} for sophomores that got housing.")

This match got 1369 out of 1369 for sophomores that got housing.


In [199]:
def compute_correct_housing_allocation(student_data, allocated, room_data):
    undergrads_in_undergrad_housing = 0
    grads_in_grad_housing = 0
    total_undergrads = sum(student_data['student_year'].isin(['Freshman', 'Sophomore', 'Junior', 'Senior']))
    total_grads = sum(student_data['student_year'].isin(['Masters', 'Doctorate']))
    allo = -1
    for student_ruid in allocated['RUID']:
        allo += 1
        room_info = allocate.loc[allo,'Assigned Rooms']
        if pd.isna(room_info):
            allo -= 1
            continue
        room_info_str = allocated[allocated['RUID'] == student_ruid]['Assigned Rooms'].item()
        building, subbuilding, roomid = [x.strip().replace('[', '').replace(']', '').replace("'", "") for x in room_info_str.split(",")]

        if subbuilding == 'nan':
            room_info = room_data[(room_data.hall_id == building) & (room_data.room_id == roomid)].reset_index().iloc[0]
        else:
            room_info = room_data[(room_data.hall_id == building) & (room_data.room_id == roomid) & (room_data.building_id == subbuilding)].reset_index().iloc[0]
        
        student_info = student_data[student_data['RUID'] == student_ruid].head(1).iloc[0]

        if student_info['student_year'] in ['Freshman', 'Sophomore', 'Junior', 'Senior'] and 'Undergraduate' in room_info['room_contract_type']:
            undergrads_in_undergrad_housing += 1
        elif student_info['student_year'] in ['Masters', 'Doctorate'] and 'Graduate' in room_info['room_contract_type']:
            grads_in_grad_housing += 1

    return undergrads_in_undergrad_housing, grads_in_grad_housing, total_undergrads, total_grads

undergrads_correctly_housed, grads_correctly_housed, total_undergrads, total_grads = compute_correct_housing_allocation(dataset, allocate, room_data)

print(f"this match got {undergrads_correctly_housed} out of {total_undergrads} for undergraduates placed in undergrad housing.")
print(f"this match got {grads_correctly_housed} out of {total_grads} for graduates placed in grad housing.")


this match got 3753 out of 4746 for undergraduates placed in undergrad housing.
this match got 515 out of 515 for graduates placed in grad housing.
